In [34]:
import numpy as np
import pandas as pd
import geopandas as gpd
from matplotlib import pyplot as plt
import os
import random
from geopy.distance import geodesic
from plotly import express as px
import json 
import plotly.graph_objects as go
import geopandas as gpd
import os
import folium

# Water contaminant data

In [35]:
contaminants_xl = pd.ExcelFile('../Datos Nacionales/BaseNacional-Ladr-Agua-Mina.xlsx')


# water
contaminants_all = pd.read_excel(contaminants_xl,'Agua')
contaminants_all['tipo'] = 'agua'

# has null values; replacing with 0s for now
cols_to_replace = ['Acrilonitrilo', 'Benceno', 'Arsenico_Total', 'Cadmio_Total', 'Arsenico_Soluble', 'Cadmio_Soluble']

# super dataframe

contaminants_all[cols_to_replace] = contaminants_all[cols_to_replace].fillna(0)

# if the dataframe has a trace amount of a measurement, cast it as 0
for col in ['Arsenico_Total', 'Cadmio_Total', 'Arsenico_Soluble', 'Cadmio_Soluble']:
    contaminants_all[col] = np.where(contaminants_all[col].str.startswith('<'), 0, contaminants_all[col])
    contaminants_all[col] = pd.to_numeric(contaminants_all[col], errors='coerce')
# contaminants_all['Cadmio_Total'] = contaminants_all['Cadmio_Total'].replace("<0.001301", 0).astype(float)


print(type(contaminants_all['Arsenico_Total'].iloc[0]))

<class 'numpy.float64'>


In [36]:
from folium.plugins import MarkerCluster
from IPython.display import display

# Create a base map centered on Mexico
m = folium.Map(location=[23.6345, -102.5528], zoom_start=5, tiles='OpenStreetMap')

# Create a MarkerCluster to group nearby points
# marker_cluster = MarkerCluster().add_to(m)

# Define a color mapping for the 'tipo' column
color_mapping = {
    'Arsenico_Total': 'blue',
    'Cadmio_Total' : 'red',
    'Arsenico_Soluble' : 'green',
    'Cadmio_Soluble' : 'yellow',
    ('Arsenico_Total', 'Arsenico_Soluble') : 'teal',
    ('Arsenico_Total', 'Cadmio_Total') : 'purple',
    ('Cadmio_Total', 'Cadmio_Soluble') : 'orange',
    ('Arsenico_Total', 'Cadmio_Total', 'Arsenico_Soluble') : 'brown'
}

contaminants_all_plot = contaminants_all[contaminants_all[['Arsenico_Total', 'Cadmio_Total', 'Arsenico_Soluble', 'Cadmio_Soluble']].max(axis=1) > 0]

# Iterate through the contaminants_all_plot DataFrame
for _, row in contaminants_all_plot.iterrows():
    # Get the latitude, longitude, and type
    lat = row['Y']
    lon = row['X']
    row_short = row[['Arsenico_Total', 'Cadmio_Total', 'Arsenico_Soluble', 'Cadmio_Soluble']]
    non_zero_elements = {key: value for key, value in row_short.items() if value != 0}
    if len(non_zero_elements) == 1:
       tipo = next(iter(non_zero_elements.items()))
       size = 12 * tipo[1] / contaminants_all_plot.loc[:,tipo[0]].max()
       tipo = tipo[0] 
    else: 
        size = 12 * np.sum(list(non_zero_elements.values())) / np.sum(contaminants_all_plot.loc[:,list(non_zero_elements.keys())].max(axis=0))
        tipo = tuple(non_zero_elements.keys())
    
    municipio = row['MUNICIPIO']
    
    # Get the color for the marker
    color = color_mapping.get(tipo, 'gray')
    
    # Add a marker to the map
    folium.CircleMarker(
        location=[lat, lon],
        radius=size,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.6,
        popup=f"Municipio: {municipio[0].upper() + municipio[1:].lower()}<br>High concentrations: {non_zero_elements}"
    ).add_to(m)

# Define the legend as an HTML string
legend_html = '''
<div style="
    position: fixed; 
    bottom: 10px; left: 10px; width: 200px; height: auto; 
    background-color: white; border:2px solid grey; z-index:9999; font-size:12px;
    padding: 5px; border-radius: 3px;">
    <b>High concentrations</b><br>
    <i style="background:blue; width:10px; height:10px; display:inline-block;"></i> Total Arsenic<br>
    <i style="background:red; width:10px; height:10px; display:inline-block;"></i> Total Cadmium<br>
    <i style="background:green; width:10px; height:10px; display:inline-block;"></i> Soluble Arsenic<br>
    <i style="background:teal; width:10px; height:10px; display:inline-block;"></i> Total and Soluble Arsenic<br>
    <i style="background:orange; width:10px; height:10px; display:inline-block;"></i> Total and Soluble Cadmium<br>
</div>
'''

# Add the legend to the map
m.get_root().html.add_child(folium.Element(legend_html))

# Save and display the map
display(m)
m.save('water.html')